In [1]:
import numpy as np 
import pandas as pd 
import sys 
import matplotlib.pyplot as plt

from DataManager import DataManager 
import setting as st 

def normalize_data(X):
    mu = np.mean(X, axis=0)
    sigma = np.std(X, axis=0)
    X_n = (X - mu) / sigma
    return X_n, mu, sigma

def norm_eq(X, y):
    theta = np.dot(np.dot(np.linalg.pinv(np.dot(X.T, X)), X.T), y)
    return theta

def shuffle_index(X, y):
    m, n = X.shape
    sidx = np.random.permutation(m)
    return sidx, X[sidx], y[sidx]

def chunk_validation_set(portion, X, y):
    m, n = X.shape
    sidx, sX, sy = shuffle_index(X, y)
    nval = int(portion*m)
    trainX = X[nval:]
    trainy = y[nval:]
    valX = X[0:nval]
    valy = y[0:nval]
    return trainX, trainy, valX, valy

def remove_non_positive_data(X, y):
    Xmask = np.all(X > 0, axis=1)
    ymask = np.all(y > 0, axis=1)
    mask = Xmask & ymask
    return X[mask], y[mask]

def remove_strange_data(X, y):
    Xmask = np.all(X < 300, axis=1)
    ymask = np.all(y < 300, axis=1)
    mask = Xmask & ymask
    return X[mask], y[mask]

def preprocess_data(X, y):
    X, y = remove_non_positive_data(X, y)
    X, y = remove_strange_data(X, y)
    return X, y 


def predict(theta, instance):
    h_theta = np.dot(instance, theta)
    return h_theta

def h(X, theta):
    return np.dot(X, theta)

def J(theta, h, lamb, X, y):
    m, n = X.shape
    square_error = np.sum((h(X, theta) - y)**2)
    regularization = lamb * np.dot(theta[1:].T, theta[1:])
    return (1 / 2) * (1 / m) * (square_error + regularization)

def gradient_descent(theta, h, X, y, eta, lamb, n_iters):
    m, n = X.shape
    theta_record = np.zeros((n_iters, *theta.shape))
    loss_record = np.zeros((n_iters, 1))
    
    theta_record[0] = theta
    loss_record[0] = J(theta, h, lamb, X, y)
    grad_square_sum = np.zeros(theta.shape)
    for i in range(1, n_iters):
        total_grad = np.dot(X.T, (h(X, theta) - y))
        total_grad[1:] = total_grad[1:] + lamb * theta[1:]
        grad = (1 / m) * total_grad
        
        grad_square_sum = grad**2 + grad_square_sum
        
        theta = theta - eta * grad / np.sqrt(grad_square_sum)
        theta_record[i] = theta
        loss_record[i] = J(theta, h, lamb, X, y)
        print('iteration:', i, 'loss:', loss_record[i])
        
    return theta, theta_record, loss_record

def initialize_theta_randomly(X, y):
    m, n = X.shape
    return np.random.normal(loc=0, scale=1, size=(n, 1))

def initialize_theta_to_zero(X, y):
    m, n = X.shape
    return np.zeros((n, 1))

def initialize_theta(X, y):
    return norm_eq(X, y)

def find_example_error(theta, h, J, lamb, X, y):
    error_list = []

    for i, example in enumerate(zip(X, y)):
        xx, yy = example
        xx = xx.reshape((1, -1))
        yy = yy.reshape((1, 1))
        error_list.append((J(theta, h, lamb, xx, yy), i, xx, yy))

    return sorted(error_list, reverse=True)

def validate_data(rate, h, J, X, y):
    lamb = 0
    norm_theta = norm_eq(X, y)
    error_list = sorted(find_example_error(norm_theta, h, J, lamb, X, y), reverse=True)
    to_drop = error_list[0:int(rate*len(error_list))]
    to_drop_idx = [idx for err, idx, xx, yy in to_drop]
    return np.delete(X, to_drop_idx, axis=0), np.delete(y, to_drop_idx, axis=0)


def main():
    dm = DataManager()

    dm.read_training_data(st.TRAINING_SET)

    mdfs = dm.select_feature_to_mdfs(st.SELECTED_FEATURE)

    X, y = dm.chunk_examples(mdfs, chunk_size=st.CHUNK_SIZE)

    X, y = preprocess_data(X, y)

    X_n, mu, sigma = normalize_data(X)

    X_n = np.insert(X_n, obj=0, values=1, axis=1)

    X_n, y = validate_data(st.VALIDATE_RATE, h, J, X_n, y)

    init_theta = initialize_theta_to_zero(X_n, y)

    theta, theta_record, loss_record = gradient_descent(init_theta, h, X_n, y, eta=st.ETA, lamb=st.LAMBDA, n_iters=st.N_ITERS)

    np.save(st.MODEL_NAME, theta)
    np.save(st.STATISTICS, np.array([mu, sigma]))
    
#     fig, ax = plt.subplots()
#     ax.set_title('final loss:'+str(loss_record[-1]))
#     ax.plot(np.arange(loss_record.size), loss_record)
#     plt.savefig('p2_eta%f.png'%(st.ETA))


In [2]:
print(st.SELECTED_FEATURE, st.ETA, st.LAMBDA, st.CHUNK_SIZE, st.N_ITERS)

['PM2.5'] 0.1 0.001 9 200000


In [3]:
main()

iteration: 1 loss: [ 537.99295964]
iteration: 2 loss: [ 528.38646395]
iteration: 3 loss: [ 520.89110339]
iteration: 4 loss: [ 514.63877184]
iteration: 5 loss: [ 509.22719728]
iteration: 6 loss: [ 504.43169364]
iteration: 7 loss: [ 500.11188435]
iteration: 8 loss: [ 496.17321155]
iteration: 9 loss: [ 492.54843258]
iteration: 10 loss: [ 489.18772905]
iteration: 11 loss: [ 486.05298792]
iteration: 12 loss: [ 483.11428812]
iteration: 13 loss: [ 480.34763533]
iteration: 14 loss: [ 477.73344263]
iteration: 15 loss: [ 475.25547752]
iteration: 16 loss: [ 472.90011138]
iteration: 17 loss: [ 470.6557718]
iteration: 18 loss: [ 468.51253439]
iteration: 19 loss: [ 466.46181313]
iteration: 20 loss: [ 464.49612169]
iteration: 21 loss: [ 462.60888664]
iteration: 22 loss: [ 460.79429964]
iteration: 23 loss: [ 459.04719893]
iteration: 24 loss: [ 457.36297343]
iteration: 25 loss: [ 455.73748433]
iteration: 26 loss: [ 454.16700048]
iteration: 27 loss: [ 452.64814471]
iteration: 28 loss: [ 451.17784883]
it

iteration: 406 loss: [ 335.77376921]
iteration: 407 loss: [ 335.63739545]
iteration: 408 loss: [ 335.50123573]
iteration: 409 loss: [ 335.36528926]
iteration: 410 loss: [ 335.22955528]
iteration: 411 loss: [ 335.09403302]
iteration: 412 loss: [ 334.95872171]
iteration: 413 loss: [ 334.82362059]
iteration: 414 loss: [ 334.68872892]
iteration: 415 loss: [ 334.55404593]
iteration: 416 loss: [ 334.41957089]
iteration: 417 loss: [ 334.28530306]
iteration: 418 loss: [ 334.1512417]
iteration: 419 loss: [ 334.01738608]
iteration: 420 loss: [ 333.88373547]
iteration: 421 loss: [ 333.75028916]
iteration: 422 loss: [ 333.61704642]
iteration: 423 loss: [ 333.48400654]
iteration: 424 loss: [ 333.35116883]
iteration: 425 loss: [ 333.21853256]
iteration: 426 loss: [ 333.08609704]
iteration: 427 loss: [ 332.95386159]
iteration: 428 loss: [ 332.82182549]
iteration: 429 loss: [ 332.68998808]
iteration: 430 loss: [ 332.55834866]
iteration: 431 loss: [ 332.42690656]
iteration: 432 loss: [ 332.2956611]
ite

iteration: 636 loss: [ 308.88270301]
iteration: 637 loss: [ 308.78152147]
iteration: 638 loss: [ 308.68045014]
iteration: 639 loss: [ 308.57948876]
iteration: 640 loss: [ 308.47863705]
iteration: 641 loss: [ 308.37789477]
iteration: 642 loss: [ 308.27726166]
iteration: 643 loss: [ 308.17673746]
iteration: 644 loss: [ 308.07632191]
iteration: 645 loss: [ 307.97601476]
iteration: 646 loss: [ 307.87581575]
iteration: 647 loss: [ 307.77572463]
iteration: 648 loss: [ 307.67574115]
iteration: 649 loss: [ 307.57586506]
iteration: 650 loss: [ 307.47609611]
iteration: 651 loss: [ 307.37643404]
iteration: 652 loss: [ 307.27687861]
iteration: 653 loss: [ 307.17742957]
iteration: 654 loss: [ 307.07808668]
iteration: 655 loss: [ 306.97884969]
iteration: 656 loss: [ 306.87971834]
iteration: 657 loss: [ 306.78069241]
iteration: 658 loss: [ 306.68177164]
iteration: 659 loss: [ 306.5829558]
iteration: 660 loss: [ 306.48424464]
iteration: 661 loss: [ 306.38563791]
iteration: 662 loss: [ 306.28713539]
it

iteration: 991 loss: [ 278.42486795]
iteration: 992 loss: [ 278.35136422]
iteration: 993 loss: [ 278.27791578]
iteration: 994 loss: [ 278.20452255]
iteration: 995 loss: [ 278.13118443]
iteration: 996 loss: [ 278.05790134]
iteration: 997 loss: [ 277.98467319]
iteration: 998 loss: [ 277.91149989]
iteration: 999 loss: [ 277.83838135]
iteration: 1000 loss: [ 277.76531749]
iteration: 1001 loss: [ 277.69230821]
iteration: 1002 loss: [ 277.61935344]
iteration: 1003 loss: [ 277.54645307]
iteration: 1004 loss: [ 277.47360703]
iteration: 1005 loss: [ 277.40081523]
iteration: 1006 loss: [ 277.32807758]
iteration: 1007 loss: [ 277.255394]
iteration: 1008 loss: [ 277.1827644]
iteration: 1009 loss: [ 277.11018869]
iteration: 1010 loss: [ 277.03766679]
iteration: 1011 loss: [ 276.96519861]
iteration: 1012 loss: [ 276.89278407]
iteration: 1013 loss: [ 276.82042308]
iteration: 1014 loss: [ 276.74811556]
iteration: 1015 loss: [ 276.67586142]
iteration: 1016 loss: [ 276.60366058]
iteration: 1017 loss: [ 

iteration: 1337 loss: [ 255.78934323]
iteration: 1338 loss: [ 255.7308364]
iteration: 1339 loss: [ 255.67236358]
iteration: 1340 loss: [ 255.61392474]
iteration: 1341 loss: [ 255.55551983]
iteration: 1342 loss: [ 255.49714881]
iteration: 1343 loss: [ 255.43881163]
iteration: 1344 loss: [ 255.38050827]
iteration: 1345 loss: [ 255.32223867]
iteration: 1346 loss: [ 255.26400279]
iteration: 1347 loss: [ 255.2058006]
iteration: 1348 loss: [ 255.14763205]
iteration: 1349 loss: [ 255.0894971]
iteration: 1350 loss: [ 255.03139571]
iteration: 1351 loss: [ 254.97332784]
iteration: 1352 loss: [ 254.91529345]
iteration: 1353 loss: [ 254.8572925]
iteration: 1354 loss: [ 254.79932494]
iteration: 1355 loss: [ 254.74139075]
iteration: 1356 loss: [ 254.68348986]
iteration: 1357 loss: [ 254.62562226]
iteration: 1358 loss: [ 254.56778789]
iteration: 1359 loss: [ 254.50998672]
iteration: 1360 loss: [ 254.45221871]
iteration: 1361 loss: [ 254.39448381]
iteration: 1362 loss: [ 254.33678198]
iteration: 1363 

...

iteration: 198510 loss: [ 14.3424064]
iteration: 198511 loss: [ 14.34240612]
iteration: 198512 loss: [ 14.34240584]
iteration: 198513 loss: [ 14.34240556]
iteration: 198514 loss: [ 14.34240528]
iteration: 198515 loss: [ 14.342405]
iteration: 198516 loss: [ 14.34240472]
iteration: 198517 loss: [ 14.34240444]
iteration: 198518 loss: [ 14.34240416]
iteration: 198519 loss: [ 14.34240388]
iteration: 198520 loss: [ 14.3424036]
iteration: 198521 loss: [ 14.34240332]
iteration: 198522 loss: [ 14.34240304]
iteration: 198523 loss: [ 14.34240275]
iteration: 198524 loss: [ 14.34240247]
iteration: 198525 loss: [ 14.34240219]
iteration: 198526 loss: [ 14.34240191]
iteration: 198527 loss: [ 14.34240163]
iteration: 198528 loss: [ 14.34240135]
iteration: 198529 loss: [ 14.34240107]
iteration: 198530 loss: [ 14.34240079]
iteration: 198531 loss: [ 14.34240051]
iteration: 198532 loss: [ 14.34240023]
iteration: 198533 loss: [ 14.34239995]
iteration: 198534 loss: [ 14.34239967]
iteration: 198535 loss: [ 14.

iteration: 198864 loss: [ 14.34230749]
iteration: 198865 loss: [ 14.34230721]
iteration: 198866 loss: [ 14.34230694]
iteration: 198867 loss: [ 14.34230666]
iteration: 198868 loss: [ 14.34230638]
iteration: 198869 loss: [ 14.3423061]
iteration: 198870 loss: [ 14.34230582]
iteration: 198871 loss: [ 14.34230555]
iteration: 198872 loss: [ 14.34230527]
iteration: 198873 loss: [ 14.34230499]
iteration: 198874 loss: [ 14.34230471]
iteration: 198875 loss: [ 14.34230443]
iteration: 198876 loss: [ 14.34230416]
iteration: 198877 loss: [ 14.34230388]
iteration: 198878 loss: [ 14.3423036]
iteration: 198879 loss: [ 14.34230332]
iteration: 198880 loss: [ 14.34230304]
iteration: 198881 loss: [ 14.34230277]
iteration: 198882 loss: [ 14.34230249]
iteration: 198883 loss: [ 14.34230221]
iteration: 198884 loss: [ 14.34230193]
iteration: 198885 loss: [ 14.34230166]
iteration: 198886 loss: [ 14.34230138]
iteration: 198887 loss: [ 14.3423011]
iteration: 198888 loss: [ 14.34230082]
iteration: 198889 loss: [ 14

iteration: 199166 loss: [ 14.34222388]
iteration: 199167 loss: [ 14.3422236]
iteration: 199168 loss: [ 14.34222333]
iteration: 199169 loss: [ 14.34222305]
iteration: 199170 loss: [ 14.34222278]
iteration: 199171 loss: [ 14.3422225]
iteration: 199172 loss: [ 14.34222223]
iteration: 199173 loss: [ 14.34222195]
iteration: 199174 loss: [ 14.34222167]
iteration: 199175 loss: [ 14.3422214]
iteration: 199176 loss: [ 14.34222112]
iteration: 199177 loss: [ 14.34222085]
iteration: 199178 loss: [ 14.34222057]
iteration: 199179 loss: [ 14.3422203]
iteration: 199180 loss: [ 14.34222002]
iteration: 199181 loss: [ 14.34221975]
iteration: 199182 loss: [ 14.34221947]
iteration: 199183 loss: [ 14.34221919]
iteration: 199184 loss: [ 14.34221892]
iteration: 199185 loss: [ 14.34221864]
iteration: 199186 loss: [ 14.34221837]
iteration: 199187 loss: [ 14.34221809]
iteration: 199188 loss: [ 14.34221782]
iteration: 199189 loss: [ 14.34221754]
iteration: 199190 loss: [ 14.34221727]
iteration: 199191 loss: [ 14.

iteration: 199464 loss: [ 14.34214206]
iteration: 199465 loss: [ 14.34214179]
iteration: 199466 loss: [ 14.34214152]
iteration: 199467 loss: [ 14.34214124]
iteration: 199468 loss: [ 14.34214097]
iteration: 199469 loss: [ 14.3421407]
iteration: 199470 loss: [ 14.34214042]
iteration: 199471 loss: [ 14.34214015]
iteration: 199472 loss: [ 14.34213988]
iteration: 199473 loss: [ 14.3421396]
iteration: 199474 loss: [ 14.34213933]
iteration: 199475 loss: [ 14.34213906]
iteration: 199476 loss: [ 14.34213878]
iteration: 199477 loss: [ 14.34213851]
iteration: 199478 loss: [ 14.34213824]
iteration: 199479 loss: [ 14.34213796]
iteration: 199480 loss: [ 14.34213769]
iteration: 199481 loss: [ 14.34213742]
iteration: 199482 loss: [ 14.34213714]
iteration: 199483 loss: [ 14.34213687]
iteration: 199484 loss: [ 14.3421366]
iteration: 199485 loss: [ 14.34213632]
iteration: 199486 loss: [ 14.34213605]
iteration: 199487 loss: [ 14.34213578]
iteration: 199488 loss: [ 14.3421355]
iteration: 199489 loss: [ 14.

iteration: 199757 loss: [ 14.34206228]
iteration: 199758 loss: [ 14.34206201]
iteration: 199759 loss: [ 14.34206174]
iteration: 199760 loss: [ 14.34206147]
iteration: 199761 loss: [ 14.3420612]
iteration: 199762 loss: [ 14.34206093]
iteration: 199763 loss: [ 14.34206065]
iteration: 199764 loss: [ 14.34206038]
iteration: 199765 loss: [ 14.34206011]
iteration: 199766 loss: [ 14.34205984]
iteration: 199767 loss: [ 14.34205957]
iteration: 199768 loss: [ 14.3420593]
iteration: 199769 loss: [ 14.34205903]
iteration: 199770 loss: [ 14.34205876]
iteration: 199771 loss: [ 14.34205849]
iteration: 199772 loss: [ 14.34205821]
iteration: 199773 loss: [ 14.34205794]
iteration: 199774 loss: [ 14.34205767]
iteration: 199775 loss: [ 14.3420574]
iteration: 199776 loss: [ 14.34205713]
iteration: 199777 loss: [ 14.34205686]
iteration: 199778 loss: [ 14.34205659]
iteration: 199779 loss: [ 14.34205632]
iteration: 199780 loss: [ 14.34205605]
iteration: 199781 loss: [ 14.34205578]
iteration: 199782 loss: [ 14